In [1]:
%matplotlib widget
from IPython.display import display, HTML
display(HTML("<style>.container{width:100% !important;}</style>"))

import matplotlib.pyplot as plt


## VarShapeSet and BitArrayShape

A general quadratic unconstrained binary optimization problem takes the form
$$
\min_X \sum_{i=0}^{N-1} h_i x_i + \sum_{i=0}^{N-2} \sum_{j=i+1}^{N-1} w_{ij} x_i x_j,
$$
with $X = (x_0,\ldots,x_{N-1}) \in \{0,1\}^N$ and problem parameters $h_i,w_{ij}\in \mathbb{R}$ for $i,j\in \{0,\ldots, N-1\}$.
In most real world problems, each entry in the bit vector to optimize has a broader meaning like point in time or space. 
Even more, in many optimization problems, a single index is not enough, but a double or triple index is needed.

In order to get around complicated index transformations, we want to implement the qubos with help of a `VarShapeSet` and a `BitArrayShape`.

Below, you find implemented a `numpy.ndarray` object `my_constant_bits` for a two dimension problem.
Such an object can be used to define constant bits in a problem in an elegant and comfortable way. A minus one in the array means that the corresponding bit is not fixed but variable, and as such part of the annealing which does the optimization.
A zero in the constant bit array means that the corresponding bit is fixed to False (or zero), and a one means that it is fixed to True (or one).
Such bits will not be part of the annealing. 
All forth and back transformations of flat indices are done internally by the library.

In [2]:
from dadk.QUBOSolverCPU import *
from dadk.Solution_SolutionList import *
from dadk.BinPol import *

my_constant_bits = np.full((5,5), -1, np.int8)

my_bit_shape_array = BitArrayShape(name='test_array', shape=(5,5), axis_names=['x','y'], constant_bits=my_constant_bits) 

my_varshapeset = VarShapeSet(my_bit_shape_array)

In [3]:
my_constant_bits

array([[-1, -1, -1, -1, -1],
       [-1, -1, -1, -1, -1],
       [-1, -1, -1, -1, -1],
       [-1, -1, -1, -1, -1],
       [-1, -1, -1, -1, -1]], dtype=int8)

In [4]:
print(my_bit_shape_array)

"test_array" (5, 5)  ['x', 'y']


### Example: Adding Linear Terms

In [5]:
Pol=BinPol(my_varshapeset)
for j in range(4):
    Pol.add_term(1,("test_array",j,j+1))
print(Pol)

x_1 + x_7 + x_13 + x_19


In [ ]:
Pol.add_term(1,(1,))

### Example: Adding Cuadratic Terms

In [6]:
Pol=BinPol(my_varshapeset)
for j in range(4):
    Pol.add_term(1,("test_array",j+1,j+1),("test_array",j,j))
print(Pol)

x_0 x_6 + x_6 x_12 + x_12 x_18 + x_18 x_24


# Slack Variables

# VarSlack

In quadratic constraint binary optimization problems, one frequently wants to express inequality conditions with respect to a constant, e.g.
$$
x_0 + x_1 \leq 2.
$$
Such statements cannot simply be formulated in a relaxed way and added to the optimization target as is done for equality constraints. Therefore, we need another way to convert a problem with inequality conditions into a polynomial that expresses a quadratic unconstrained binary optimization problem (QUBO).
To this aim, a helper variable called `slack variable` is introduced. This variable obtains auxiliary bits which express a bit variable that can take values within a certain range. One then converts the inequality constraint to an equality constraint with respect to the slack variable.
In the example above, the slack variable $S$ could be defined as $S = x_2 + x_3,$ and thus would be able to take values in $\{0,1,2\}$. The corresponding equality constraint would be
$$
x_0 + x_1 - S = 0.
$$
This constraint can then be added to the optimization target as
$$
C (x_0 + x_1 - S)^2,
$$
with $C>0$ large enough, and minimization of this additional term enforces the original inequality constraint 
$$
x_0 + x_1 \leq 2.
$$

The slack variable $S$ could be implemented with help of a `BitShapeArray` object.
However, since slack variables are used frequently, there already exits a class `VarSlack`.
As for `BitShapeArray` objects, a `VarSlack` is initialized with a `name`.
Moreover, the range to be represented by the variable is specified by keyword arguments `start`, `stop` and `step`, as for the built in `range` function.
Finally, the `slack_type` is specified. It denotes the way in which the desired range is represented. 
For example, `slack_type = SlackType.unary` gives rise to a unary slack variable $S = \sum_{i=0}^N x_i$, whereas `slack_type = SlackType.binary` stands for a binary variable of the form $S = \sum_{i=0}^N 2^i x_i$, with appropriate $N\geq0$. The binary representation needs less bits than the unary representation, which gets important for large problem instances when bits are rare or if the range to represent is large.

There also exist the slack types `SlackType.sequential`, `SlackType.littlegauss` and `SlackType.fibonacci` which you can experiment with below.
Your first task in this exercise is to define a `VarSlack` object representing the values $\{0,1,2,\ldots,63\}$.
Try different slack types and observe the effect on the `length` attribute of the object. This tells you how many bits will be needed for the variable.

Next, define a `VarShapeSet` containing your slack variable. Afterwards, initialize a `BinPol` object `qubo` based on your `VarShapeSet` and add the slack variable by calling the `add_slack_variable` method of the BinPol object with the name of the slack variable as parameter.
Print your BinPol object for different slack types and observe the different representations of the range $\{0,1,2,\ldots,63\}$.

In [8]:
from random import randint

my_var_slack = VarSlack(name='slack_variable',start=0,step=1,stop=63,slack_type=SlackType.binary)
print(f"Length of the slack variable: {my_var_slack.length}")

var_shape_set = VarShapeSet(my_var_slack) 
qubo = BinPol(var_shape_set).add_slack_variable('slack_variable')
print(f"Qubo representation of the slack variable: {qubo}")

Length of the slack variable: 6
Qubo representation of the slack variable: x_0 + 2.0 x_1 + 4.0 x_2 + 8.0 x_3 + 16.0 x_4 + 31.0 x_5


## Knapsack problem

The knapsack problem or rucksack problem is a problem in combinatorial optimization: Given a set of items, each with a weight and a value, select a collection of items so that the total load is less than or equal to a given limit and the total value is as large as possible.

$N$ is the total number of items to choose from.

$V=(v_0,v_1,...v_{N-1})$ is the vector of values of the $N$ items.

$W=(w_0,w_1,...w_{N-1})$ is the vector of weights of the $N$ items.

$L$ is the maximal load your knapsack will carry.

The aim is to maximize the value within the given load limit, i.e.:

Find $C \subset \{0,1,...N-1\}$ with $\sum_{i \in C} w_i \le L$

such that for all $D \subset \{0,1,...N-1\}$ with $\sum_{i \in D} w_i \le L$

First, we will solve the problem considering the equality instead of the inequality:

for all $D \subset \{0,1,...N-1\}$ with $\sum_{i \in D} w_i = L$

### Equality Constraint

#### Setting the input

In [ ]:
profits = [12, 15, 80, 36, 20, 21, 30]
weights = [100, 300, 210, 650, 500, 300, 200]
C = 15
max_weight = 1000

#### Creating the variable set

In [ ]:
var_shape_set = VarShapeSet(BitArrayShape('x', shape=(len(profits),)))
BinPol.freeze_var_shape_set(var_shape_set)

#### Defining the QUBO model

In [ ]:
profit_p = BinPol()
for p in range(len(profits)):
    profit_p.add_term(-profits[p],('x',p))

weight_p = BinPol()
for w in range(len(weights)):
    weight_p.add_term(weights[w],('x',w))
weight_p.add_term(-max_weight,())
weight_p.power(2)

QUBO=profit_p+C*weight_p

#### Solving the Problem

In [ ]:
from dadk.QUBOSolverCPU import *

solver = QUBOSolverCPU(
number_iterations=200000,
number_runs=10,
scaling_bit_precision=32,
auto_tuning=AutoTuning.AUTO_SCALING_AND_SAMPLING)
            
solution_list = solver.minimize(QUBO)

print(solution_list.solver_times)

#### Ploting the Solution

In [ ]:
print("Profit term value is %s \n" % profit_p.compute(solution_list.min_solution.configuration)) 
print("Constraint term value is %s \n" % weight_p.compute(solution_list.min_solution.configuration)) 

In [ ]:
my_bit_array = solution_list.min_solution.extract_bit_array('x')
my_bit_array.draw(axis_names=['x'])

### Exercise: Program the former model considering the <= Constraint instead of the = Constraint

#### Setting the input

In [ ]:
profits = [12, 15, 80, 36, 20, 21, 30]
weights = [100, 300, 210, 650, 500, 300, 200]
C = 15
max_weight = 1000

#### Creating the variable set

In [ ]:
items = BitArrayShape('x',shape=(len(profits),))
# Create the slack variable
## Code here


##

BinPol.freeze_var_shape_set(VarShapeSet(items, slack))

print(f'Y = {slack.qubo}')

#### Defining the QUBO model

In [ ]:
profit_p = BinPol()
for p in range(len(profits)):
    profit_p.add_term(-profits[p],('x',p))


weight_p = BinPol()
# Create the weight term
## Code here


##


    
QUBO=profit_p+C*weight_p

#### Solving the Problem

In [ ]:
from dadk.QUBOSolverCPU import *

solver = QUBOSolverCPU(
number_iterations=200000,
number_runs=10,
scaling_bit_precision=32,
auto_tuning=AutoTuning.AUTO_SCALING_AND_SAMPLING)
            
solution_list = solver.minimize(QUBO)

print(solution_list.solver_times)

#### Ploting the Solution

In [ ]:
print("Profit term value is %s \n" % profit_p.compute(solution_list.min_solution.configuration)) 
print("Constraint term value is %s \n" % weight_p.compute(solution_list.min_solution.configuration)) 

In [ ]:
my_bit_array = solution_list.min_solution.extract_bit_array('s')
my_bit_array.draw(axis_names=['s'])

In [ ]:
sol_array = list(solution_list.min_solution.extract_bit_array('x').data)

In [ ]:
def display(selection,max_load,values,weights):
    size=len(selection)
    sel = 0
    weight = 0
    value = 0
    print("\nItem Sel Value  Weight")
    for n in range(size):
        print(" %3d %2.1s %5d %5d" % (n, 'Y' if selection[n]==1 else 'N', values[n], weights[n]))
        if selection[n]==1:
            sel += 1
            value += values[n]
            weight += weights[n]
    print("Sum %3d %5d %5d\n" % (sel, value, weight))
    if weight > max_load:
        print("Maximum load of %d exceeded by %d units!" % (max_load, weight - max_load))
    else:
        print("%.2f%% of maximum load of %d units used" % (weight * 100.0 / max_load, max_load))

In [ ]:
display(sol_array,max_weight,profits,weights)